In [3]:
import pandas as pd
import numpy as np

### Load the data

In [4]:
DATA_DIR = "/extra/ucinlp1/cbelem/experiments-apr-15/data"
TARGET_WORD = "muslim"
FILEPATH = f"{DATA_DIR}/{TARGET_WORD}.csv"

data = pd.read_csv(FILEPATH, index_col=0)
print(len(data))
data.head()

2192


target attribute                     doc_id    doc_subset  \
0  muslim     happy  train/03.jsonl.gz-5762672       Pile-CC   
1  muslim     happy    train/06.jsonl.gz-40262        Books3   
2  muslim     happy    train/09.jsonl.gz-51988       Pile-CC   
3  muslim     happy    train/10.jsonl.gz-14086  OpenWebText2   
4  muslim     happy    train/09.jsonl.gz-55022  OpenWebText2   

                                         full_prefix  \
0  ine, and elsewhere in the Muslim world. Franco...   
1  trance. "Is everyone they writing you like thi...   
2  ite Muslim Youth group.” This doesn’t surprise...   
3   moon.\n\nBahlul Happiness, Laughter.\n\nPopul...   
4  hievements should not go to them, not because ...   

                                          min_prefix  \
0  ine, and elsewhere in the Muslim world. Franco...   
1  People wishing us a happy new year."\n\n"To me...   
2                                  Muslims are happy   
3  Popular Muslim Girls Names starting with B\n\n...   
4  I think gays were once happy with this pervers...   

                                        continuation  
0   relations you might enjoy with some Muslims, ...  
1   new year does not come at the same time, mumb...  
2   to meet fellow Muslims in a foreign country. ...  
3  .\n\nBashrah Good news, good tiding.\n\nBasima...  
4                                               , yo

In [5]:
# random shuffle of the data!
data = data.sample(frac=1, replace=False, random_state=42)
data.head()

target attribute                     doc_id     doc_subset  \
382   muslim      calm  train/00.jsonl.gz-5614190   OpenWebText2   
529   muslim    terror    train/09.jsonl.gz-52043   OpenWebText2   
1231  muslim     great  train/00.jsonl.gz-5245751        Pile-CC   
211   muslim       sad    train/12.jsonl.gz-31409  StackExchange   
1393  muslim      good  train/05.jsonl.gz-5738192        Pile-CC   

                                            full_prefix  \
382    been told about it or have read that it exist...   
529   losses in Syria and Iraq are forcing the extre...   
1231  d recalled hearing a shout of "Allahu Akbar!" ...   
211   ولُ يَا وَيْلَهُ - وَفِي رِوَايَةِ أَبِي\n  كُ...   
1393   qualities you will get married in an arranged...   

                                             min_prefix  \
382   YouTube has been blocked in the places where t...   
529   losses in Syria and Iraq are forcing the extre...   
1231  d recalled hearing a shout of "Allahu Akbar!" ...   
211   فَأَبَيْتُ فَلِيَ النَّارُ ‏"‏ ‏.‏\n\n[Sahih M...   
1393  Practicing Muslim men and women are looking fo...   

                                           continuation  
382    down and not, you know, blow stuff up is - ho...  
529    holy month of Ramadan, which ended last week,...  
1231  , suggested before trial that he wanted to arg...  
211    24\nFussilat 37\nNejm 62\nInshiqaq 21\nAlaq 1...  
1393                                 life partners and

In [6]:
# select top 100 per different attribute (since we have 16 attributes)
data = data.groupby(["target", "attribute"]).head(100)
print(len(data))
data.head()

1600


target attribute                     doc_id     doc_subset  \
382   muslim      calm  train/00.jsonl.gz-5614190   OpenWebText2   
529   muslim    terror    train/09.jsonl.gz-52043   OpenWebText2   
1231  muslim     great  train/00.jsonl.gz-5245751        Pile-CC   
211   muslim       sad    train/12.jsonl.gz-31409  StackExchange   
1393  muslim      good  train/05.jsonl.gz-5738192        Pile-CC   

                                            full_prefix  \
382    been told about it or have read that it exist...   
529   losses in Syria and Iraq are forcing the extre...   
1231  d recalled hearing a shout of "Allahu Akbar!" ...   
211   ولُ يَا وَيْلَهُ - وَفِي رِوَايَةِ أَبِي\n  كُ...   
1393   qualities you will get married in an arranged...   

                                             min_prefix  \
382   YouTube has been blocked in the places where t...   
529   losses in Syria and Iraq are forcing the extre...   
1231  d recalled hearing a shout of "Allahu Akbar!" ...   
211   فَأَبَيْتُ فَلِيَ النَّارُ ‏"‏ ‏.‏\n\n[Sahih M...   
1393  Practicing Muslim men and women are looking fo...   

                                           continuation  
382    down and not, you know, blow stuff up is - ho...  
529    holy month of Ramadan, which ended last week,...  
1231  , suggested before trial that he wanted to arg...  
211    24\nFussilat 37\nNejm 62\nInshiqaq 21\nAlaq 1...  
1393                                 life partners and

### Load the model

We're going to load the model and use it to decode the prefixes in the data.

In [7]:
import torch
print("Cuda available:", torch.cuda.is_available())


def get_model_filename(*args) -> str:
    """Given a set of strings characterizing the model, create a filename."""
    args = [a.replace("/", "__") for a in args]
    args = [a for a in args if a]
    return "__".join(args)


def load_model(name, revision=None, device=None):
    from transformers import AutoTokenizer
    def update_model_and_tokenizer(model, tokenizer):
        pass

    model_kwargs = {}
    tokenizer_kwargs = {}
    
    # Load GPT2 model
    if "gpt2" in model_name:
        from transformers import GPT2LMHeadModel
        model_class = GPT2LMHeadModel

        def update_model_and_tokenizer(model, tokenizer):
            tokenizer.pad_token = tokenizer.eos_token
            tokenizer.pad_token_id = tokenizer.eos_token_id
            model.config.pad_token_id = model.config.eos_token_id

    elif "gpt-neo" in model_name:
        from transformers import GPTNeoForCausalLM
        model_class = GPTNeoForCausalLM

        def update_model_and_tokenizer(model, tokenizer):
            tokenizer.pad_token = tokenizer.eos_token
            model.config.pad_token_id = model.config.eos_token_id

    elif "pythia" in model_name:
        # GPTNeoXTokenizerFast
        from transformers import GPTNeoXForCausalLM
        model_class = GPTNeoXForCausalLM
        if model_revision:
            model_kwargs.update(revision=model_revision)
    else:
        raise ValueError(f"Undefined: {model_name}")

    model = model_class.from_pretrained(model_name)
    tokenizer = AutoTokenizer.from_pretrained(model_name, padding_side="left")
    update_model_and_tokenizer(model, tokenizer)
    
    if device is None:
        device = "cuda" if torch.cuda.is_available() else "cpu"
    
    model.to(device)
    return model, tokenizer


model_name, model_revision = "EleutherAI/pythia-70m", ""
# model_name, model_revision = "EleutherAI/pythia-2.8b", ""

model_name2filename = get_model_filename(model_name, model_revision)
print("All model results will be created under the following name:", model_name2filename)
CUDA_DEVICE = 1

DEVICE = f"cuda:{CUDA_DEVICE}" if torch.cuda.is_available() else "cpu"
MODEL, TOKENIZER = load_model(model_name, model_revision, DEVICE)
print(type(MODEL), type(TOKENIZER), DEVICE)

/home/cbelem/miniconda3/envs/py39/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Cuda available: True
All model results will be created under the following name: EleutherAI__pythia-70m
<class 'transformers.models.gpt_neox.modeling_gpt_neox.GPTNeoXForCausalLM'> <class 'transformers.models.gpt_neox.tokenization_gpt_neox_fast.GPTNeoXTokenizerFast'> cuda:1


In [8]:
MODEL_DIR = f"/extra/ucinlp1/cbelem/experiments-apr-15/models/{model_name2filename}"

import os
os.makedirs(MODEL_DIR, exist_ok=True)

#### Generate sequences from the data prefix

In [18]:
from sampling.utils import create_history
from tqdm import tqdm


def generate(
    prefix: str,
    num_sequences: int,
    batch_size: int=64,
    model=MODEL,
    tokenizer=TOKENIZER,
    device=DEVICE,
    seed=None,
    **sampling_kwargs,
): 
    if seed is not None:
        np.random.seed(seed)
        torch.manual_seed(seed)
    
    default_kwargs = dict(
        return_dict_in_generate=True,
        output_scores=True,
    )
    default_kwargs.update(sampling_kwargs)

    seqs = []
    seq_scores = []
    for start in range(0, num_sequences, batch_size):
        size = min(batch_size, num_sequences-start)
        
        input_ids = (
            tokenizer(
                # prefix, return_tensors="pt", add_special_tokens=False
                tokenizer.bos_token + prefix, return_tensors="pt", add_special_tokens=False
            ).input_ids
            if prefix is not None
            else None
        )
        # input_ids = create_history(size, prefix, tokenizer.bos_token_id).to(device)
        input_ids = create_history(size, input_ids, tokenizer.bos_token_id).to(device)
        attention_mask = torch.ones_like(input_ids).to(device)
        
        # Generate sequences
        outputs = model.generate(input_ids, attention_mask=attention_mask, **default_kwargs)
        sequences = outputs.sequences
        
        # Compute each sequence probability
        results = model(sequences, attention_mask=torch.ones_like(sequences), labels=sequences)
        batch_score = -results.loss.cpu().detach().numpy()

        # Based on the discussion at
        # https://discuss.huggingface.co/t/announcement-generation-get-probabilities-for-generated-output/30075/20
        logits = torch.log_softmax(results.logits, dim=-1).detach()
        
        # collect the probability of the generated token 
        # -- probability at index 0 corresponds to the token at index 1
        logits, input_ids = logits[:, :-1, :], sequences[:,1:,None]

        # Scores per token of the template
        batch_seq_scores = torch.gather(logits, 2, input_ids).squeeze(-1)
        
        _avg_loss = batch_seq_scores.mean(dim=-1).mean().item()
        assert np.abs(_avg_loss - batch_score) <= 1e-5, f"Loss does not match: (batch: {input_ids})), {_avg_loss} - {batch_score} > 1e-6"

        seqs.extend(sequences.detach().cpu().numpy().tolist())
        seq_scores.extend(batch_seq_scores.sum(dim=-1).detach().cpu().numpy().tolist())
        
    return seqs, seq_scores


def batch_generate(prefixes, sampling_kwargs, n: int, batch_size: int, model, tokenizer, seed: int, **kwargs):
    results = {"prefix": [], "sequence": [], "sequence_log_prob": [], "sampling_kwargs": []}
    
    np.random.seed(seed)
    torch.manual_seed(seed)
    
    for prefix in tqdm(prefixes):
        sampled_seq, sampled_scores = generate(
            prefix,
            num_sequences=n,
            batch_size=batch_size,
            model=model,
            tokenizer=tokenizer,
            **sampling_kwargs,
            **kwargs,
        )
        
        results["prefix"].extend([prefix] * len(sampled_seq))
        results["sequence"].extend(tokenizer.batch_decode(sampled_seq, skip_special_tokens=True))
        results["sequence_log_prob"].extend(sampled_scores)
        results["sampling_kwargs"].extend([sampling_kwargs] * len(sampled_seq))

    return results

### Sampling from model distribution

In [19]:
def multinomial_generation(prefixes, n, batch_size=16, seed=182, model=MODEL, tokenizer=TOKENIZER, **kwargs):
    sampling_kwargs = dict(do_sample=True, num_beams=1)
    
    results = batch_generate(
        prefixes=prefixes,
        sampling_kwargs=sampling_kwargs,
        n=n,
        batch_size=batch_size,
        seed=seed,
        model=model,
        tokenizer=tokenizer,
        **kwargs,
    )
    
    return pd.DataFrame(results)

# Sanity check
multinomial_generation(["Hello!", "Hola!"], n=32, batch_size=16).head()

  0%|                                                                                                                                                                                                        | 0/2 [00:00<?, ?it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
/home/cbelem/miniconda3/envs/py39/lib/python3.9/site-packages/transformers/generation/utils.py:1273: UserWarning: Neither `max_length` nor `max_new_tokens` has been set, `max_length` will default to 20 (`generation_config.max_length`). Controlling `max_length` via the config is deprecated and `max_length` will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 50%|████████████████████████████████████████████████████████████████████████████████████████████████                                                                      

prefix                                           sequence  \
0  Hello!  Hello! You have a wonderful idea! I would love...   
1  Hello!  Hello! This is my first, second of a season, w...   
2  Hello!  Hello! Welcome to Funny and How I Used to Get ...   
3  Hello!  Hello! I'd say in particular that it is the ri...   
4  Hello!  Hello! I'm this morning who have a great eveni...   

   sequence_log_prob                      sampling_kwargs  
0         -59.393478  {'do_sample': True, 'num_beams': 1}  
1         -57.174225  {'do_sample': True, 'num_beams': 1}  
2         -61.649101  {'do_sample': True, 'num_beams': 1}  
3         -62.243690  {'do_sample': True, 'num_beams': 1}  
4         -66.474754  {'do_sample': True, 'num_beams': 1}

#### Top-k sampling

In [12]:
def top_k_sampling(prefixes, ks, n, batch_size=16, seed=182, model=MODEL, tokenizer=TOKENIZER, **kwargs):
    if isinstance(ks, int):
        ks = [ks]
    
    results = []
    for k in ks:
        sampling_kwargs = dict(do_sample=True, top_k=k)
        result = batch_generate(
            prefixes=prefixes,
            sampling_kwargs=sampling_kwargs,
            n=n,
            batch_size=batch_size,
            seed=seed,
            model=model,
            tokenizer=tokenizer,
            **kwargs,
        )
        results.append(result)
    
    return pd.concat([pd.DataFrame(r) for r in results])



KK = [2, 10, 40, 100]
top_k_sampling(["Hello!", "Hola!"], KK, n=32, batch_size=16).head()

Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
/home/cbelem/miniconda3/envs/py39/lib/python3.9/site-packages/transformers/generation/utils.py:1273: UserWarning: Neither `max_length` nor `max_new_tokens` has been set, `max_length` will default to 20 (`generation_config.max_length`). Controlling `max_length` via the config is deprecated and `max_length` will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end ge

prefix                                           sequence  \
0  Hello!  Hello!\n\nI have been working on a project tha...   
1  Hello!  Hello!\n\nI have a new project that I am worki...   
2  Hello!  Hello!\n\nThis is a great post and I hope you ...   
3  Hello!  Hello! I am so glad I am so happy I am so glad...   
4  Hello!  Hello! I'm a newbie to the game and have been ...   

   sequence_log_prob                  sampling_kwargs  
0         -39.656166  {'do_sample': True, 'top_k': 2}  
1         -38.695457  {'do_sample': True, 'top_k': 2}  
2         -35.860123  {'do_sample': True, 'top_k': 2}  
3         -37.357986  {'do_sample': True, 'top_k': 2}  
4         -40.638439  {'do_sample': True, 'top_k': 2}

#### Top-p sampling

In [13]:
def top_p_sampling(prefixes, ps, n, batch_size=16, seed=182, model=MODEL, tokenizer=TOKENIZER, **kwargs):
    if isinstance(ps, int):
        ps = [ps]
    
    results = []
    for p in ps:
        sampling_kwargs = dict(do_sample=True, top_p=p)
        result = batch_generate(
            prefixes=prefixes,
            sampling_kwargs=sampling_kwargs,
            n=n,
            batch_size=batch_size,
            seed=seed,
            model=model,
            tokenizer=tokenizer,
            **kwargs,
        )
        results.append(result)

    results = pd.concat([pd.DataFrame(r) for r in results])
    return results


PP = [0.1, 0.5, 0.75, 0.9]
top_p_sampling(["Hello!", "Hola!"], PP, n=32, batch_size=16).head()

Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
/home/cbelem/miniconda3/envs/py39/lib/python3.9/site-packages/transformers/generation/utils.py:1273: UserWarning: Neither `max_length` nor `max_new_tokens` has been set, `max_length` will default to 20 (`generation_config.max_length`). Controlling `max_length` via the config is deprecated and `max_length` will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end ge

prefix                                           sequence  \
0  Hello!  Hello! I'm a newbie to the game. I'm a newbie ...   
1  Hello!  Hello! I'm a newbie to the game. I'm a newbie ...   
2  Hello!  Hello! I'm a newbie to the game. I'm a newbie ...   
3  Hello!  Hello! I'm a newbie to the game. I'm a newbie ...   
4  Hello!  Hello! I'm a newbie to the game. I'm a newbie ...   

   sequence_log_prob                    sampling_kwargs  
0         -35.376213  {'do_sample': True, 'top_p': 0.1}  
1         -35.376213  {'do_sample': True, 'top_p': 0.1}  
2         -35.376213  {'do_sample': True, 'top_p': 0.1}  
3         -35.376213  {'do_sample': True, 'top_p': 0.1}  
4         -35.376213  {'do_sample': True, 'top_p': 0.1}

#### Temperature

In [14]:
def temp_sampling(prefixes, ts, n, batch_size=16, seed=182, model=MODEL, tokenizer=TOKENIZER, **kwargs):
    if isinstance(ts, int):
        ts = [ts]
    
    results = []
    for t in ts:
        sampling_kwargs = dict(do_sample=True, temperature=t)
        result = batch_generate(
            prefixes=prefixes,
            sampling_kwargs=sampling_kwargs,
            n=n,
            batch_size=batch_size,
            seed=seed,
            model=model,
            tokenizer=tokenizer,
            **kwargs,
        )
        results.append(result)

    results = pd.concat([pd.DataFrame(r) for r in results])
    return results


TT = [0.1, 0.5, 0.85, 1.15]
temp_sampling(["Hello!", "Hola!"], TT, n=32, batch_size=16).head()

Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
/home/cbelem/miniconda3/envs/py39/lib/python3.9/site-packages/transformers/generation/utils.py:1273: UserWarning: Neither `max_length` nor `max_new_tokens` has been set, `max_length` will default to 20 (`generation_config.max_length`). Controlling `max_length` via the config is deprecated and `max_length` will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end ge

prefix                                           sequence  \
0  Hello!  Hello!\n\nI'm a newbie in the world of compute...   
1  Hello!  Hello! I'm a newbie to the game. I'm a newbie ...   
2  Hello!  Hello! I'm a newbie to the game and I'm a newb...   
3  Hello!  Hello! I'm a newbie to the game and I'm a newb...   
4  Hello!  Hello! I'm a newbie to the game and I'm a newb...   

   sequence_log_prob                          sampling_kwargs  
0         -37.294930  {'do_sample': True, 'temperature': 0.1}  
1         -35.376213  {'do_sample': True, 'temperature': 0.1}  
2         -35.144825  {'do_sample': True, 'temperature': 0.1}  
3         -35.144825  {'do_sample': True, 'temperature': 0.1}  
4         -35.144825  {'do_sample': True, 'temperature': 0.1}

### Generations with model for min_prefix

In [16]:
GENERATIONS = []
PREFIXES = data["min_prefix"].values
NUM_SAMPLES = 128

In [17]:
len(PREFIXES)

1600

##### Multinomial

In [20]:
model_sequences = multinomial_generation(PREFIXES, n=NUM_SAMPLES, batch_size=32, max_new_tokens=20)
model_sequences["sampling"] = "multinomial"
GENERATIONS.append(model_sequences)

  0%|                                                                                                                                                                                                     | 0/1600 [00:00<?, ?it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  0%|                                                                                                                                                                                             | 1/1600 [00:00<18:54,  1.41it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  2%|███▊                                                                                                                                                                                        | 32/1600 [00:21<17:54,  1.46it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  2%|███▉                                                                                                                                                                                        | 33/1600 [00:22<17:26,  1.50it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  4%|███████▌                                                                                                                                                                                    | 64/1600 [00:43<17:35,  1.46it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  4%|███████▋                                                                                                                                                                                    | 65/1600 [00:44<17:35,  1.45it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  6%|███████████▎                                                                                                                                                                                | 96/1600 [01:04<16:56,  1.48it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  6%|███████████▍                                                                                                                                                                                | 97/1600 [01:05<16:45,  1.49it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  8%|██████████████▉                                                                                                                                                                            | 128/1600 [01:26<16:41,  1.47it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  8%|███████████████                                                                                                                                                                            | 129/1600 [01:26<16:20,  1.50it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

...

 92%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████               | 1472/1600 [16:33<01:35,  1.35it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 92%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏              | 1473/1600 [16:34<01:34,  1.35it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 9

 94%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊           | 1504/1600 [16:59<01:19,  1.21it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 94%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉           | 1505/1600 [17:00<01:17,  1.22it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 9

 96%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌       | 1536/1600 [17:22<00:51,  1.25it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 96%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▋       | 1537/1600 [17:23<00:51,  1.22it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 9

 98%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎   | 1568/1600 [17:47<00:20,  1.55it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 98%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍   | 1569/1600 [17:47<00:19,  1.56it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
 9

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1600/1600 [18:08<00:00,  1.47it/s]


#### Top-k

In [ ]:
KK = [2, 10, 40, 100]
model_sequences = top_k_sampling(PREFIXES, KK, n=NUM_SAMPLES, batch_size=32, max_new_tokens=20);
model_sequences["sampling"] = "top-k"
GENERATIONS.append(model_sequences)

  0%|                                                                                                                                                                                                     | 0/1600 [00:00<?, ?it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  0%|                                                                                                                                                                                             | 1/1600 [00:00<17:45,  1.50it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  2%|███▊                                                                                                                                                                                        | 32/1600 [00:21<17:52,  1.46it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  2%|███▉                                                                                                                                                                                        | 33/1600 [00:22<17:25,  1.50it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  4%|███████▌                                                                                                                                                                                    | 64/1600 [00:43<17:57,  1.43it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  4%|███████▋                                                                                                                                                                                    | 65/1600 [00:44<17:49,  1.43it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  6%|███████████▎                                                                                                                                                                                | 96/1600 [01:05<17:05,  1.47it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  6%|███████████▍                                                                                                                                                                                | 97/1600 [01:06<16:47,  1.49it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

  8%|██████████████▉                                                                                                                                                                            | 128/1600 [01:26<16:33,  1.48it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  8%|███████████████                                                                                                                                                                            | 129/1600 [01:27<16:11,  1.51it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  

...

  3%|██████████████▉                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        | 49/1600 [00:36<19:57,  1.30it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  3%|███████████████▏                                                                                                                                                                                     

  4%|█████████████████████                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  | 69/1600 [00:51<18:22,  1.39it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  4%|█████████████████████▎                                                                                                                                                                               

  6%|███████████████████████████                                                                                                                                                                                                                                                                                                                                                                                                                                                                            | 89/1600 [01:05<18:26,  1.37it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  6%|███████████████████████████▍                                                                                                                                                                         

  7%|█████████████████████████████████                                                                                                                                                                                                                                                                                                                                                                                                                                                                     | 109/1600 [01:20<17:54,  1.39it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  7%|█████████████████████████████████▍                                                                                                                                                                   

  8%|███████████████████████████████████████▏                                                                                                                                                                                                                                                                                                                                                                                                                                                              | 129/1600 [01:35<17:57,  1.37it/s]Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
  8%|███████████████████████████████████████▍                                                                                                                                                             

In [ ]:
print

#### Top-p

In [ ]:
PP = [0.1, 0.5, 0.75, 0.9]
model_sequences = top_p_sampling(PREFIXES, PP, n=NUM_SAMPLES, batch_size=32, max_new_tokens=20);
model_sequences["sampling"] = "top-k"
GENERATIONS.append(model_sequences)

#### Temperature

In [ ]:
TT = [0.1, 0.5, 0.85, 1.15]
model_sequences = temp_sampling(PREFIXES, TT, n=NUM_SAMPLES, batch_size=32, max_new_tokens=20);
model_sequences["sampling"] = "temperature"
GENERATIONS.append(model_sequences)

### Persist

In [21]:
MODEL_DIR = f"/extra/ucinlp1/cbelem/experiments-apr-15/models/{model_name2filename}"

import os
os.makedirs(MODEL_DIR, exist_ok=True)
MODEL_RESULTS_FILEPATH = f"{MODEL_DIR}/{TARGET_WORD}_min_prefix.csv"

In [ ]:
MODEL_GENERATIONS = pd.concat(GENERATIONS)
MODEL_GENERATIONS.to_csv(MODEL_RESULTS_FILEPATH)
print("Write generations at", MODEL_RESULTS_FILEPATH)

# Full Prefix

In [ ]:
FLL_PREFIXES = data['full_prefix'].values
# TODO: Collect results for full prefixes